In [1]:
import pandas as pd
import numpy as np 
import glob
import os 
from datetime import datetime

In [2]:
hoje = datetime.today().strftime('%Y-%m-%d')

In [3]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")

calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)

calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]

calendario = calendario[calendario['MARCA'] == "BOTICARIO"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 3).astype(str).str.zfill(2)       #<<< MUDAR O "4" (CICLO ATUAL + 4 PARA ACHAR O CICLO DA SUGESTÃO) EX: C202505 -> C202509
ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]

# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]

filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)

filtered_calendario['match'] = 1


In [4]:
filtered_calendario

Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO      MARCA       Date  \
2283  C202512   2025-08-11 2025-08-31       21  BOTICARIO 2025-08-11   

      NUM_CICLO ANO_CICLO CICLOMAIS2  dias_ate_inicio  match  
2283         12     C2025    C202515               55      1

In [5]:
ciclo_lanc = filtered_calendario['Ciclo'].max()

In [6]:
ciclo_lanc

'C202512'

In [7]:
df_similares = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C12\LANÇAMENTOS\arquivos para geração da sugestão\SIMILARES\PRODUTOS SIMILARES - BOT.xlsx")

df_similares = pd.merge(left=df_similares,right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], how= 'left', left_on = 'CICLO SIMILAR',right_on = 'Ciclo' )

df_similares = df_similares.drop(columns=['Ciclo'])

df_similares = df_similares.rename(columns={'INICIO CICLO':'INICIO CICLO SIMILAR','FIM CICLO':'FIM CICLO SIMILAR','DURAÇÃO':'DURAÇÃO CICLO SIMILAR'})
df_similares.drop_duplicates(inplace=True)

df_similares['MATCH'] = 1

df_similares = df_similares.drop(columns=['INICIO DO CICLO',
       'FIM DO CICLO', 'DURAÇÃO CICLO','INICIO CICLO SIMILAR','FIM CICLO SIMILAR','DURAÇÃO CICLO SIMILAR'])

In [8]:
df_similares.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH'],
      dtype='object')

In [9]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C12\LANÇAMENTOS\arquivos para geração da sugestão\TABELA DE PEDIDO\Pedidos Semanais Especiais - BOT - 202512.xlsx")

df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 

df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm') | (df_tabela['Canal'] != 'Ecomm | VD') | (df_tabela['Canal'] != 'Ecomm | Loja')] 

df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")

df_tabela = df_tabela[df_tabela['Tipo de promoção'].str.contains('Lançamentos', na=False)]

In [10]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv_origi = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

In [11]:


df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO','MARCA'])

df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

#ignorando a PDV que ainda não está online
df_pdv = df_pdv[df_pdv['DESCRIÇÃO PDV'] != '23813-COMERCIO-HIB VALENTE']

df_pdv = df_pdv[df_pdv['STATUS'] != "INATIVO"]

df_pdv = df_pdv[df_pdv['STATUS'] != "MATRIZ"]

df_pdv = df_pdv[df_pdv['SUPERVISOR'] != 'Inativa']

df_pdv['MATCH'] = 1

In [12]:
df_similares = pd.merge(left=df_similares,right=df_pdv,right_on=['MATCH'],left_on=['MATCH'],how='inner')

df_similares = df_similares.drop_duplicates()

In [13]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C12\LANÇAMENTOS\arquivos para geração da sugestão\DRAFT"  # arquivo dos drafts

# Pattern to match all CSV files
csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)

df_draft['match'] = 1 

df_draft.shape


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_37548\2509858446.py:10: DtypeWarning: Columns (6,7) have mixed types. Specify dtype option on import or set low_memory=False.
  df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)


(130656, 47)

In [14]:
df_draft = df_draft.drop(columns=['Categoria'])

In [15]:
df_draft.columns[7:25]

Index(['Histórico de Vendas do Ciclo 202409',
       'Histórico de Vendas do Ciclo 202410',
       'Histórico de Vendas do Ciclo 202411',
       'Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508',
       'Histórico de Vendas do Ciclo Atual'],
      dtype='object')

In [16]:
# Define as colunas mensais
colunas_mensais = df_draft.columns[7:25]

# Agrupa por PDV e calcula crescimento médio por PDV
def calcular_crescimento(grupo):
    soma_mensal = grupo[colunas_mensais].sum()             # soma por mês
    variacao_mensal = soma_mensal.pct_change().dropna()    # variação percentual mês a mês
    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

    if len(variacao_mensal) == 0:
        return pd.Series({'CRESCIMENTO': np.nan})

    media = variacao_mensal.mean()
    desvio = variacao_mensal.std()

    limite_sup = media + 2 * desvio
    limite_inf = media - 2 * desvio

    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]
    crescimento = round(variacoes_filtradas.mean(), 4)
    return pd.Series({'CRESCIMENTO': crescimento})

# Aplica a função por PDV
crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)

# Merge do resultado de volta no dataframe original
df_draft = df_draft.merge(crescimento_por_pdv, on='PDV', how='left')


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_37548\1463083786.py:24: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)


In [17]:
df_similares['PDV'] = df_similares['PDV'].astype('Int64')

df_final = pd.merge(left=df_similares,right=df_draft,right_on=['PDV', 'SKU'],left_on=['PDV','PRODUTO SIMILAR'],how='left')

In [18]:
df_venda_diaria = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C12\LANÇAMENTOS\arquivos para geração da sugestão\VENDAS_DIARIAS\FormFiltroConsultaVendaSintetica_17_06_2025_14_04_40.xls")
df_venda_diaria.shape

(17025, 14)

In [19]:
df_venda_diaria.columns

Index(['Unidade de Negócio', 'Ano', 'Mês', 'Dia', 'Código do Produto',
       'Descrição do Produto', 'Quantidade', 'Valor Bruto', 'Valor Desconto',
       'Valor Líquido', 'Valor Vale Troca', 'Líquido - Troca', 'Estoque Atual',
       'Estoque Mínimo'],
      dtype='object')

In [20]:
df_venda_diaria['PDV'] = df_venda_diaria['Unidade de Negócio'].str.split("-").str[0].str.strip()

df_venda_diaria['Dia'] = pd.to_datetime(df_venda_diaria['Dia'], format='%d/%m/%Y')

df_venda_diaria = pd.merge(left=df_venda_diaria,right=calendario[['Ciclo','Date']],left_on='Dia',right_on='Date',how='inner')

df_venda_diaria = df_venda_diaria.drop(columns='Date')

df_venda_diaria.shape

(17025, 16)

In [21]:
# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
df_venda_diaria = df_venda_diaria.sort_values(by=['Unidade de Negócio', 'Código do Produto', 'Dia'])

# Calcula a quantidade acumulada até o dia para cada grupo
df_venda_diaria['Quantidade Acumulada'] = (
    df_venda_diaria
    .groupby(['Unidade de Negócio', 'Código do Produto'])['Quantidade']
    .cumsum()
)  # acumulado por grupo até a data da linha

df_venda_diaria.shape

(17025, 17)

In [22]:
df_venda_diaria = df_venda_diaria.drop_duplicates()

df_venda_agrupado = df_venda_diaria.fillna(0).groupby(['PDV', 'Código do Produto','Ciclo'])['Quantidade Acumulada'].max().reset_index()
df_venda_agrupado

PDV  Código do Produto    Ciclo  Quantidade Acumulada
0     12522               4522  C202312                     1
1     12522               4522  C202314                     2
2     12522               4522  C202406                     3
3     12522               4522  C202407                     4
4     12522               4522  C202410                     5
...     ...                ...      ...                   ...
5800   5699              81054  C202503                   167
5801   5699              81054  C202504                   168
5802   5699              81054  C202505                   169
5803   5699              81054  C202506                   170
5804   5699              85293  C202506                     5

[5805 rows x 4 columns]

In [23]:
df_venda_agrupado[(df_venda_agrupado['Ciclo']=='C202213')&(df_venda_agrupado['Código do Produto']==81054)&(df_venda_agrupado['PDV']=='20994')]

PDV  Código do Produto    Ciclo  Quantidade Acumulada
2955  20994              81054  C202213                    35

In [24]:
df_venda_agrupado[['Ciclo','Código do Produto','PDV']].dtypes

Ciclo                object
Código do Produto     int64
PDV                  object
dtype: object

In [25]:
df_final[['CICLO SIMILAR','PRODUTO SIMILAR','PDV']].dtypes

CICLO SIMILAR       object
PRODUTO SIMILAR    float64
PDV                  Int64
dtype: object

In [26]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], right_on='match',left_on='MATCH',how='left')
df_final.shape

(1216, 76)

In [27]:
#df_final = df_final.drop(columns=['PDV DESC','status','SKU','Descrição','Lançamento','Item analisado','Planograma','Quantidade por caixa'])

In [28]:
df_final = pd.merge(left=df_final, right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], right_on='Ciclo',left_on='CICLO SIMILAR',how='left')
df_final.shape

df_final = df_final.drop_duplicates()

In [29]:

df_venda_agrupado = df_venda_agrupado.rename(columns={'Quantidade Acumulada':'Vendas Ciclo Lançamento'})

In [30]:
df_final['PRODUTO SIMILAR'] = df_final['PRODUTO SIMILAR'].astype('Int64')

df_venda_agrupado['PDV'] = df_venda_agrupado['PDV'].astype('Int64')

df_final = pd.merge(left=df_final, right = df_venda_agrupado, right_on=['Ciclo','Código do Produto','PDV'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final = df_final.drop_duplicates()

In [31]:
df_final['Vendas Ciclo Lançamento'].sum()

np.float64(3757.0)

In [32]:
df_final = df_final[df_final['PRODUTO LANÇAMENTO'].notna()]
df_final['Vendas Ciclo Lançamento'] = df_final['Vendas Ciclo Lançamento'].fillna(0)


In [33]:
df_final['PDV'].value_counts().min()

np.int64(14)

In [34]:
df_final.columns[29:46]

Index(['Desativação', 'Histórico de Vendas do Ciclo 202409',
       'Histórico de Vendas do Ciclo 202410',
       'Histórico de Vendas do Ciclo 202411',
       'Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507'],
      dtype='object')

In [35]:
df_jacobina = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\REGIÃO JACOBINA\draft unificado.xlsx")

In [36]:
df_jacobina = df_jacobina[['PDV', 'SKU','202408', '202409',
       '202410', '202411', '202412', '202413', '202414', '202415', '202416',
       '202417', '202501', '202502', '202503', '202504', '202505', '202506',
       '202507']]

In [37]:
ciclos = [
    '202408', '202409', '202410', '202411', '202412', '202413',
    '202414', '202415', '202416', '202417', '202501', '202502',
    '202503', '202504', '202505', '202506', '202507']

df_jacobina[ciclos] = df_jacobina[ciclos].fillna(0)

In [38]:
df_final = pd.merge(left=df_final,right=df_jacobina,left_on=['PRODUTO SIMILAR','PDV'],right_on=['SKU','PDV'],how='left')

In [39]:
# Gera pares de colunas: coluna estática ↔ coluna de histórico
pares_validos = [
    (ciclo, f'Histórico de Vendas do Ciclo {ciclo}')
    for ciclo in ciclos
    if ciclo in df_final.columns and f'Histórico de Vendas do Ciclo {ciclo}' in df_final.columns
]

# Separa os nomes das colunas
colunas_estaticas = [c[0] for c in pares_validos]
colunas_historico = [c[1] for c in pares_validos]

# Aplica a regra: se valor na coluna estática for maior, sobrescreve no histórico
for col_estatica, col_hist in zip(colunas_estaticas, colunas_historico):
    df_final[col_hist] = df_final[col_estatica].where(
        df_final[col_estatica] > df_final[col_hist],
        df_final[col_hist]
    )


In [40]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[29:46]

# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

df_final['CRESCIMENTO_GERAL'] = CRESCIMENTO

CRESCIMENTO


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_37548\1328364976.py:8: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  variacao_mensal = soma_mensal.pct_change()


np.float64(0.1817)

In [41]:
df_final = df_final.drop(columns='Ciclo_y')

df_final = df_final.rename(columns={'Ciclo_x': 'Ciclo',	'INICIO CICLO_x': 'INICIO CICLO',	'FIM CICLO_x':'FIM CICLO' ,'DURAÇÃO_x':'DURAÇÃO',
                                    	'INICIO CICLO_y': 'INICIO CICLO SIMILAR' ,	'FIM CICLO_y': 'FIM CICLO SIMILAR','DURAÇÃO_y':'DURAÇÃO CICLO SIMILAR'})

In [42]:
df_final.columns[40:47]

Index(['Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504',
       'Histórico de Vendas do Ciclo 202505',
       'Histórico de Vendas do Ciclo 202506',
       'Histórico de Vendas do Ciclo 202507',
       'Histórico de Vendas do Ciclo 202508'],
      dtype='object')

In [43]:
VENDA_SIMILAR_6_MESES= df_final.columns[40:47]

df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final[VENDA_SIMILAR_6_MESES].max(axis=1)

df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final['Pico Vendas Similar Ultimos 6 ciclos'].fillna(0)

df_final['MEDIANA DO HISTÓRICO'] = df_final[colunas_mensais].median(axis=1, skipna=True)




In [44]:
df_final[colunas_mensais].median(axis=1, skipna=True)


0       1.0
1       3.5
2       0.5
3       0.0
4       1.0
       ... 
1059    0.0
1060    0.0
1061    0.0
1062    0.0
1063    0.0
Length: 1064, dtype: object

In [45]:
medi = df_final.groupby(['CANAL'])['MEDIANA DO HISTÓRICO'].max().reset_index()
medi = medi.rename(columns={'MEDIANA DO HISTÓRICO':'med_por_canal'})
medi

CANAL med_por_canal
0    CD          20.0
1   HIB           2.0
2    LJ           3.5
3    VD          10.0

In [46]:
df_final = pd.merge(left=df_final, right=medi,on='CANAL',how='inner')


In [47]:
df_vdc = pd.read_csv(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C11\arquivos para geração da sugestão\VENDAS VDC\vendas_vdc22.02.csv")



df_vdc['DATA VENDA'] = pd.to_datetime(df_vdc['DATA VENDA'])

# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
df_venda_diaria = df_venda_diaria.sort_values(by=['Unidade de Negócio', 'Código do Produto', 'Dia'])

# Calcula a quantidade acumulada até o dia para cada grupo
df_vdc['Quantidade Acumulada vdc'] = (
    df_vdc
    .groupby(['PDVDEPARA.Practico', 'Código'])['Soma de Quantidade']
    .cumsum()
)  # acumulado por grupo até a data da linha

In [48]:
df_vdc = pd.merge(left=df_vdc,right=calendario[['Date','Ciclo']],left_on='DATA VENDA',right_on='Date',how='inner')

df_vdc_agrupado = df_vdc.groupby(['PDVDEPARA.Practico',	'Código','Ciclo'])['Quantidade Acumulada vdc'].max().reset_index()

df_vdc_agrupado = df_vdc_agrupado.rename(columns={'Ciclo':'Ciclo vdc'})


df_vdc_agrupado.head()

PDVDEPARA.Practico  Código Ciclo vdc  Quantidade Acumulada vdc
0               23701   48617   C202212                         6
1               23701   48617   C202213                         8
2               23701   48617   C202214                        10
3               23701   48617   C202215                        12
4               23701   48617   C202216                        22

In [49]:
df_final = pd.merge(left=df_final, right = df_vdc_agrupado, right_on=['Ciclo vdc','Código','PDVDEPARA.Practico'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final['Quantidade Acumulada vdc'] = df_final['Quantidade Acumulada vdc'].fillna(0)


df_final['Vendas Ciclo Lançamento'] = np.where(df_final['Quantidade Acumulada vdc'] > 0, df_final['Quantidade Acumulada vdc'], df_final['Vendas Ciclo Lançamento'])

df_final = df_final.drop(columns='Quantidade Acumulada vdc')


df_final = df_final.drop(columns='Ciclo vdc')



In [50]:

# Cálculo do crescimento
crescimento_final = df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']
crescimento_final = crescimento_final.clip(lower=0.2, upper=0.8)  # limita entre 0 e 0.8
df_final['CRESCIMENTO_FINAL'] = crescimento_final

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_FINAL'].isna(),df_final['CRESCIMENTO_GERAL'],df_final['CRESCIMENTO_FINAL'])

df_final['CRESCIMENTO_FINAL'] = df_final['CRESCIMENTO_FINAL'].fillna(0)

df_final['MEDIANA DO HISTÓRICO'] = df_final['MEDIANA DO HISTÓRICO'].fillna(0)

# Corrige mediana do histórico onde for zero
df_final['MEDIANA DO HISTÓRICO'] = np.where(
    df_final['MEDIANA DO HISTÓRICO'] == 0,
    df_final['med_por_canal'],
    df_final['MEDIANA DO HISTÓRICO']
)

df_final['MEDIANA DO HISTÓRICO'] = df_final['MEDIANA DO HISTÓRICO'].fillna(0)



# Cálculo do PV GINSENG
pv_crescimento = (df_final['CRESCIMENTO_FINAL']+1) * df_final['Vendas Ciclo Lançamento']
pv_mediana = (df_final['CRESCIMENTO_FINAL'] + 1) * df_final['MEDIANA DO HISTÓRICO']

df_final['PV GINSENG'] = np.where(
    pv_crescimento < df_final['MEDIANA DO HISTÓRICO'],
    pv_mediana.round(0),
    pv_crescimento.round(0)
)

# Se PV GINSENG for NA, substitui pela média por canal
df_final['PV GINSENG'] = df_final['PV GINSENG'].fillna(df_final['med_por_canal'].round(0))

df_final['PV GINSENG'] = df_final['PV GINSENG'].round(0).astype(int)

df_final.shape


C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_37548\2817892533.py:10: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df_final['MEDIANA DO HISTÓRICO'] = df_final['MEDIANA DO HISTÓRICO'].fillna(0)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_37548\2817892533.py:19: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df_final['MEDIANA DO HISTÓRICO'] = df_final['MEDIANA DO HISTÓRICO'].fillna(0)


(1022, 108)

In [51]:
df_final.to_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C12\LANÇAMENTOS\validação.xlsx",index=False)

In [52]:
df_final.columns[30:43]

Index(['Histórico de Vendas do Ciclo 202409',
       'Histórico de Vendas do Ciclo 202410',
       'Histórico de Vendas do Ciclo 202411',
       'Histórico de Vendas do Ciclo 202412',
       'Histórico de Vendas do Ciclo 202413',
       'Histórico de Vendas do Ciclo 202414',
       'Histórico de Vendas do Ciclo 202415',
       'Histórico de Vendas do Ciclo 202416',
       'Histórico de Vendas do Ciclo 202417',
       'Histórico de Vendas do Ciclo 202501',
       'Histórico de Vendas do Ciclo 202502',
       'Histórico de Vendas do Ciclo 202503',
       'Histórico de Vendas do Ciclo 202504'],
      dtype='object')

In [53]:
df_final.drop(columns=df_final.columns[30:43],inplace=True)

In [54]:
df_final = df_final.rename(columns={df_final.columns[30]: "C-4", df_final.columns[31]: "C-3",df_final.columns[32]: "C-2",df_final.columns[33]: "C-1",df_final.columns[34]:'VENDAS CICLO ATUAL'})


In [55]:
df_final.columns = df_final.columns.str.upper()

df_final.drop(columns=df_final.filter(regex='HISTÓRICO DE VENDAS DO CICLO').columns, inplace=True)

df_final.columns

Index(['PRODUTO LANÇAMENTO', 'DESCRIÇÃO DO LANÇAMENTO', 'PRODUTO SIMILAR',
       'DESCRIÇÃO SIMILAR', 'CICLO SIMILAR', 'FOCO', 'IAF', 'CATEGORIA',
       'MARCA', '% CONSUMIDOR', 'MECANICA CONSUMIDOR', '% REVENDEDOR',
       'MECANICA REVENDEDOR', 'TIPO DE PRODUTO', 'MATCH', 'PDV',
       'PDV COMO TEXTO', 'CANAL', 'DESCRIÇÃO PDV', 'PDV DESC', 'UF',
       'ANALISTA', 'SUPERVISOR', 'STATUS', 'CLASSE', 'SKU_X', 'DESCRIÇÃO',
       'SUBCATEGORIA', 'LANÇAMENTO', 'DESATIVAÇÃO', 'C-4', 'C-3', 'C-2', 'C-1',
       'VENDAS CICLO ATUAL', 'DIAS SEM VENDA', 'PROJEÇÃO PRÓXIMO CICLO',
       'PROJEÇÃO PRÓXIMO CICLO + 1', 'PROMOÇÃO PRÓXIMO CICLO',
       'PROMOÇÃO PRÓXIMO CICLO + 1', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'COMPRA INTELIGENTE SEMANAL/SUGESTÃO DE COMPRA',
       'COMPRA INTELIGENTE PRÓXIMO CICLO',
       'COMPRA INTELIGENTE PRÓXIMO CICLO + 1', 'ITEM DESATIVADO',
       'DATA PREVISTA REGULARIZAÇÃO', 'CARTEIRA BLOQUEADA PARA NOVOS PEDIDOS',
       'PLANOGRA

In [56]:
df_final.shape

(1022, 94)

In [57]:
df_final[['C-4', 'C-3', 'C-2', 'C-1', 'VENDAS CICLO ATUAL']] = df_final[['C-4', 'C-3', 'C-2', 'C-1', 'VENDAS CICLO ATUAL']].fillna(0)

In [58]:
df_final = df_final[[
    'SUPERVISOR',
    'ANALISTA', 
    'CANAL',
    'UF',
    'PDV',
    'DESCRIÇÃO PDV',
    'PRODUTO LANÇAMENTO',
    'DESCRIÇÃO DO LANÇAMENTO',
    'MARCA',
    'CATEGORIA',
    'MECANICA CONSUMIDOR',
    '% CONSUMIDOR',
    'MECANICA REVENDEDOR',
    '% REVENDEDOR',
    'TIPO DE PRODUTO',
    'IAF',
    'FOCO',
    'PRODUTO SIMILAR',
    'DESCRIÇÃO SIMILAR',
    'CICLO SIMILAR',
    'VENDAS CICLO LANÇAMENTO',
    'C-4',
    'C-3',
    'C-2',
    'C-1',
    'VENDAS CICLO ATUAL',
    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG'
]]

In [59]:
df_final = df_final[[
    'SUPERVISOR',
    'ANALISTA', 
    'CANAL',
    'UF',
    'PDV',
    'DESCRIÇÃO PDV',
    'PRODUTO LANÇAMENTO',
    'DESCRIÇÃO DO LANÇAMENTO',
    'MARCA',
    'CATEGORIA',
    'MECANICA CONSUMIDOR',
    '% CONSUMIDOR',
    'MECANICA REVENDEDOR',
    '% REVENDEDOR',
    'TIPO DE PRODUTO',
    'IAF',
    'FOCO',
    'PRODUTO SIMILAR',
    'DESCRIÇÃO SIMILAR',
    'CICLO SIMILAR',
    'VENDAS CICLO LANÇAMENTO',
    'C-4',
    'C-3',
    'C-2',
    'C-1',
    'VENDAS CICLO ATUAL',
    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG'
]]

In [60]:
df_final = df_final.reindex(columns=[
    'SUPERVISOR',
    'ANALISTA',
    'CANAL',
    'UF',
    'PDV',
    'DESCRIÇÃO PDV',
    'PRODUTO LANÇAMENTO',
    'DESCRIÇÃO DO LANÇAMENTO',
    'MARCA',
    'CATEGORIA',
    'MECANICA CONSUMIDOR',
    '% CONSUMIDOR',
    'MECANICA REVENDEDOR',
    '% REVENDEDOR',
    'TIPO DE PRODUTO',
    'IAF',
    'FOCO',
    'PRODUTO SIMILAR',
    'DESCRIÇÃO SIMILAR',
    'CICLO SIMILAR',
    'VENDAS CICLO LANÇAMENTO',
    'C-4',
    'C-3',
    'C-2',
    'C-1',
    'VENDAS CICLO ATUAL',
    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG'])


In [61]:
df_final['SUGESTÃO METASELLIN'] = ''
df_final['SUGESTÃO ABASTECIMENTO'] = ''
df_final['SUGESTÃO COMERCIAL'] = ''


In [62]:
df_final.to_excel(f'C:/Users/joao.herculano/Documents/Lançamento{hoje}{ciclo_lanc}.xlsx',index=False)